## Matricule & noms : 

### <center> ELE8812 - Traitement et analyse d'images </center>
<center> Travail practique No. 4 </center>
<h3> <center> Analyse multirésolution et transformée de ondelettes</center></h3>
<center>Hiver 2024 </center>



Assurez-vous de compléter tout endroit où il est écrit `Inscrivez votre code ici ` or `DOUBLE-CLIQUEZ POUR INSCRIVE VOTRE RÉPONSE`.

<br></br>    

Ce travail pratique est consacré à l’un des principaux outils utilisés en analyse multirésolution de signaux ou d’images numériques : la transformée en ondelettes rapide. Les tâches demandées vous permettront de vous familiariser avec cet outil et de l’utiliser dans un but précis : la correction de défauts localisés dans une image.


Les fonctions Python et les données à utiliser pour effectuer ce travail pratique se trouvent dans l’archive <I>TP4.zip</I> disponible sur le site web du cours.

<b>Pondération</b> 
   - Transformée en ondelettes rapide d’une image : 8 pts
   - Correction de défauts localisés : 10 pts
   - Qualités de la langue et du rapport : 2 pts  
<b>Total : 20 points</b> 
    
    
**Date de remise**
   - Groupe 1: 8 avril 23h59
   - Groupe 2: 22 avril 23h59


## Transformée en ondelettes rapide avec Python.
    
On rappelle que prendre la transformée en ondelettes rapide (TOR) 2D d’une image consiste à la décomposer en quatre éléments dont la taille est sensiblement le quart de celle de l’image originale. Trois de ces éléments sont les coefficients de détail (respectivement horizontal, diagonal et vertical) et le quatrième élément est l’approximation de l’image originale à l’échelle immédiatement supérieure. Cette décomposition est équivalente à un codage en sous-bandes 2D, les coefficients de détail correspondant aux fréquences hautes et l’approximation aux fréquences basses. Le processus de décomposition peut être itéré sur l’approximation pour obtenir une décomposition multiéchelles ou espace-échelle. Pour effectuer une telle décomposition, les paramètres à spécifier sont l’ondelette (ou la fonction d’échelle) utilisée et le nombre de niveaux de décomposition (ou le nombre d’échelles).
      
    

La boîte à outils « pywt (PyWavelets) » de Python fournit plusieurs fonctions permettant de calculer et de manipuler la TOR d’un signal ou d’une image. Les coefficients de la TOR sont retournés dans le format suivant: [cAn, (cHn, cVn, cDn), … (cH1, cV1, cD1)] où n est le niveau de résolution, A est l'approximation de l'image originale, H est le coefficient de détails horizontal, V est le coefficient de détails vertical et D le coefficient de détails diagonal. Dans le cadre de ce travail pratique, les fonctions suivantes présentent un intérêt particulier :


| Fontion  | La description |
|:------:|:------:|
| Wavelet  | Permet d'accéder, grâce à leurs noms, aux différentes ondelettes |
| Wavelet.filter_bank | Calcul des filtres de codage-décodage en sous-bandes correspondant à une ondelette donnée |
| wavedec2 | Calcul de la TOR 2D |
| waverec2 | Calcul de la TOR 2D inverse |

Pour plus d'information sur l'utilisation de ces fonctions, consultez la documentation pour [Wavelet](https://pywavelets.readthedocs.io/en/latest/ref/wavelets.html) et pour [wavedec2 et waverec2](https://pywavelets.readthedocs.io/en/latest/ref/2d-dwt-and-idwt.html).
De plus, plusieurs fonctions permettant de manipuler et d’afficher les éléments d’une TOR 2D sont fournies. Le tableau suivant en donne une description succincte :

| Fontion  | La description |
|:------:|:------:|
| waveextract | Extraction d’un élément d’une structure TOR 2D |
| waveinsert | Insertion d’un élément dans une structure TOR 2D |
| wave2gray | Affichage pyramidal d’une structure TOD 2D |

Dans ce travail pratique, on n’utilisera que deux types d’ondelettes : les ondelettes de Daubechies (db<b>x</b>) et les ondelettes symétriques (sym<b>x</b>). Dans la désignation des ondelettes, <b>x</b> représente leur taille, qui est égale à la moitié de la longueur du support des filtres de codage-décodage en sous-bandes. De plus, l’ondelette db1 représente l’ondelette de Haar.


In [350]:
# Installation de PyWavelets la librairie d'ondelettes de Python
import sys
!{sys.executable} -m pip install PyWavelets

In [351]:
import pywt
import matplotlib.pyplot as plt
import numpy as np
from matplotlib.pyplot import imread
%matplotlib inline

In [1]:
# Fonctions utiles pour manipuler les ondelettes

def wave2gray(coefficients):
    """Affichage pyramidale d'une structure TOR 2D
     Image W:   ------- ------ ------------ -------------------
                |      |      |            |
                | a(n) | h(n) |            |
                |      |      |            |
                ------- ------     h(n-1)  |
                |      |      |            |
                | v(n) | d(n) |            |        h(n-2)
                |      |      |            |
                ------- ------ ------------
                |             |            |        
                |             |            |
                |             |            |
                |    v(n-1)   |   d(n-1)   |
                |             |            |
                |             |            |
                |             |            |
                -------------- ------------ -------------------
                |                          |
                |          v(n-2)          |        d(n-2) 
                |                          |
    
    coefficients (list): Coeffecients d'une TOR. Les coefficients renvoyés par la fonction `wavedec2` 
        peuvent être directement utilisés comme valeur d'entrée.
     
    """
    # coeffs: [cAn, (cHn, cVn, cDn), … (cH1, cV1, cD1)]
    an = coefficients[0]
    wavelets_display = an
    

    for coeff in coefficients[1:]:
        hn, vn, dn = coeff

        padding = wavelets_display.shape[0] - hn.shape[0]
        pad_y = padding // 2
        pad_x = padding - pad_y

        pad_coeff = []
        for c in [hn, vn, dn]:
            pad_coeff.append(np.pad(c, (pad_y, pad_x), 'constant', constant_values=(1, 1)))

        hn, vn, dn = pad_coeff
        wavelets_display_hn = np.concatenate([wavelets_display, hn], axis=1)
        vn_dn = np.concatenate([vn, dn], axis=1)
        wavelets_display_hn_vn_dn = np.concatenate([wavelets_display_hn, vn_dn], axis=0)
        wavelets_display = wavelets_display_hn_vn_dn

    fig, ax  = plt.subplots(1,1)
    ax.imshow(wavelets_display, cmap='gray')
    ax.set_title("Représentation pyramidale d'une structure TOR 2D")
    ax.axis('off')
    fig.set_size_inches(15,15)


def waveextract(coeffs, direction, level=0):
    """Extrait le coefficient spéficifié par les paramètres.
    
    coeffs (list): Coefficients des ondelettes.
    level (int): Niveau du coefficient à extraire.
    direction (str): Direction du coefficient à extraire. Choix: 'a', 'h', 'v' ou 'd'.
        'a': Approximation de l'image originale
        'h': Coefficient de détails horizontal
        'v': Coefficient de détails vertical
        'd': Coefficient de détails diagonal
    
    """
    if direction == 'a':
        return coeffs[0]

    dir_dict = {'h': 0, 'v': 1, 'd': 2}
    return coeffs[level][dir_dict[direction]]
    

def waveinsert(coefficients, coeff_to_insert, direction, level=0):
    """Insérer le coefficient donné à l'endroit spécifié par les paramètres.
    
    coefficients (list): Coefficients des ondelettes.
    coeff_to_insert (ndarray): Coefficient à insérer dans coeffs.
    level (int): Niveau du coefficient à insérer.
    direction (str): Direction du coefficient à insérer. Choix: 'a', 'h', 'v' ou 'd'.
        'a': Approximation de l'image originale
        'h': Coefficient de détails horizontal
        'v': Coefficient de détails vertical
        'd': Coefficient de détails diagonal
    """
    coeffs = coefficients.copy()
    if direction == 'a':
        coeffs[0] = coeff_to_insert
        return coeffs
    
    dir_dict = {'h': 0, 'v': 1, 'd': 2}
    h_v_d = []
    for d, c in enumerate(coeffs[level]):
        if dir_dict[direction] == d:
            c = coeff_to_insert
        h_v_d.append(c)
    coeffs[level] = tuple(h_v_d)
    return coeffs
    


## 1. Transformée en ondelettes rapide d’une image (8 pts)
### 1.1. Transformée directe et transformée inverse (4 pts)
Dans un premier temps, on utilise l’ondelette de Haar (db1).

<div class="alert alert-block alert-warning">
1.1.1. Représentez graphiquement la réponse impulsionnelle des filtres de codage-décodage en sous-bandes relatifs à cette ondelette. Pour vous aider, consulter la documentation <a href="https://pywavelets.readthedocs.io/en/latest/ref/wavelets.html">ici</a>. </div>

In [1]:
# Inscrivez votre code ici

<div class="alert alert-block alert-warning">
1.1.2. Effectuez et représentez la transformée en ondelettes rapide (TOR) de l’image Lenna.tif en utilisant trois niveaux d’échelle. </div>

In [2]:
# Inscrivez votre code ici

<div class="alert alert-block alert-warning">
1.1.3. Effectuez ensuite la TOR inverse et vérifiez que l’image reconstruite est identique à l’image originale aux erreurs numériques près. </div>

In [3]:
# Inscrivez votre code ici

Répétez les mêmes opérations (1.1.1. à 1.1.3) avec l’ondelette db4 aux questions 1.1.4 à 1.1.6.

<div class="alert alert-block alert-warning">
1.1.4. Représentez graphiquement la réponse impulsionnelle des filtres de codage-décodage en sous-bandes relatifs à cette ondelette. </div>

In [4]:
# Inscrivez votre code ici

<div class="alert alert-block alert-warning">
1.1.5. Effectuez et représentez la transformée en ondelettes rapide (TOR) de l’image Lenna.tif en utilisant trois niveaux d’échelle. </div>

In [5]:
# Inscrivez votre code ici

<div class="alert alert-block alert-warning">
1.1.6. Effectuez ensuite la TOR inverse et vérifiez que l’image reconstruite est identique à l’image originale aux erreurs numériques près. </div>

In [6]:
# Inscrivez votre code ici

<div class="alert alert-block alert-warning">
1.1.7. Comparez les erreurs numériques des images obtenues avec la TOR inverse des ondelettes db1 et db4. Que constatez-vous? </div>

<div class="alert alert-block alert-success"> 
DOUBLE-CLIQUEZ POUR INSCRIRE VOTRE RÉPONSE </div>

### 1.2. Utilisation des ondelettes pour la compression (4 pts)

Une approche simple de la compression d’image consiste à mettre à zéro les coefficients de détail dont la valeur absolue est inférieure à un seuil donné.

<b>Remarque :</b> Pour effectuer l’opération de seuillage des coefficients, vous pourrez utiliser `waveextract` et `waveinsert` pour extraire les coefficients de détails (avec `waveextract`), appliquer un seuillage sur les coefficients extraits et remplacer les coefficients de détails par ceux seuillés (`waveinsert`).
    
<br></br>
<div class="alert alert-block alert-warning">
1.2.1. Effectuez cette opération avec l’image et les ondelettes utilisées à la section précédente (soient l’image Lenna.tif et les ondelettes Haar & db4). </div>

In [7]:
# Inscrivez votre code ici

<div class="alert alert-block alert-warning">
1.2.2. Effectuez la TOR inverse des coefficients ainsi modifiés  
</div>

In [8]:
# Inscrivez votre code ici

<div class="alert alert-block alert-warning">
1.2.3. Évaluez l’erreur quadratique normalisée entre l’image de départ 𝐼(𝑥, 𝑦) et l’image
reconstruite 𝐼′(𝑥, 𝑦).
    
<b>Remarque:</b> L’erreur quadratique normalisée est définie par :
$$ RMS = \sqrt{ \frac { \sum_{x,y} [I(x,y)-I'(x,y)]^{2}}{ N }} $$
    
<I> N </I> représsente le nombre de pixels dans l'image. </div>

In [9]:
# Inscrivez votre code ici

<div class="alert alert-block alert-warning">
1.2.4. Évaluez le « taux de compression approché » défini comme le rapport entre nombre
de coefficients mis à zéro et le nombre total de coefficients de la TOR. </div>

In [10]:
# Inscrivez votre code ici

<div class="alert alert-block alert-warning">
1.2.5. Commentez brièvement vos résultats ainsi que l’allure des images compressées. </div>

In [11]:
# Inscrivez votre code ici

<div class="alert alert-block alert-success"> 
DOUBLE-CLIQUEZ POUR INSCRIRE VOTRE RÉPONSE </div>

## 2. Correction de défauts localisés (10 pts)
Les coefficients de la transformée en ondelettes d’une image sont liés aux caractéristiques de cette image à une position et une échelle données. Ces propriétés peuvent être utilisées pour corriger des défauts localisés tels que les rayures qui peuvent affecter les photographies argentiques. Le but de cette partie est de corriger des défauts de ce type, qui seront représentés par des segments de droite d’intensité maximale placés dans une position connue de l’image.

### 2.1. Restauration (4 pts)

Écrivez une fonction permettant de mettre à zéro (nommé `set_to_zero`) les éléments d’un tableau situés à une distance inférieure à une valeur δ d’un segment de droite AB, les coordonnées des points A et B étant spécifiées en proportion des dimensions de la matrice à laquelle ils appartiennent.


<b>Remarque :</b> On rappelle que la distance d d’un point M de coordonnées (x,y) à la droite passant par les points A et B de coordonnées respectives (x1,y1) et (x2,y2) a pour expression :

$$ d = \frac{|x(y_2 − y_1) − y(x_2 − x_1) − (x_1y_2 − x_2y_1)|}{ \sqrt{(y_2 − y_1)^2 + (x_2 − x_1)^2}} $$

In [614]:
# Inscrivez votre code ici

def set_to_zero(img, delta, line_coord):
    """ Met à zero les pixels à une distante delta ou moins de la ligne définie
    
    img (ndarray): Image à modifier.
    delta (float): Distance seuil de la ligne où les valeurs seront mises à zéro.
        La distance delta doit être entre 0 et 1 et représente une proportion de la grandeur de l'image
    line_coord (list): Liste des coordonnées des deux points par lesquels passe la droite en proportion
        des dimensions de l'image (entre 0 et 1).
        Les coordonnées doivent être présentées dans le format [Ay, Ax, By, Bx]
    
    """
    pass


<div class="alert alert-block alert-warning">
2.1.1. Calculez et représentez la transformée en ondelettes de l’image Lenna_r.tif avec l’ondelette db4. </div>

In [12]:
# Inscrivez votre code icicoeffs_db4_r = pywt.wavedec2(lenna_r, db4, level=3)

<div class="alert alert-block alert-warning">
2.1.2. À l’aide de la fonction que vous venez de développer, `set_to_zero`, mettez à zéro les coefficients de détail que vous pouvez associer à la présence du défaut.

<b>Remarque :</b> Les extrémités du défaut affectant l’image Lenna_r.tif ont les coordonnées suivantes : A = (0.1, 0.5) et B = (0.9, 0.5). </div>

In [13]:
# Inscrivez votre code ici

<div class="alert alert-block alert-info">

### 2.2. Effet du type d’ondelette (4 pts)
</div>
<div class="alert alert-block alert-warning">
2.2.1. Effectuez le même traitement qu’à la section précédente avec l’ondelette de Haar. Ajustez les paramètres à votre disposition.
</div>

In [14]:
# Inscrivez votre code ici

<div class="alert alert-block alert-warning">
2.2.2. Effectuez le même traitement qu’à la section précédente avec l’ondelette sym6. Ajustez les paramètres à votre disposition. </div>

In [15]:
# Inscrivez votre code ici

<div class="alert alert-block alert-warning">
2.2.3. Commentez les résultats obtenus. </div>

<div class="alert alert-block alert-success"> 
DOUBLE-CLIQUEZ POUR INSCRIRE VOTRE RÉPONSE </div>

<div class="alert alert-block alert-info">

### 2.3. Effet de l’orientation du défaut (2 pts)
</div>
<div class="alert alert-block alert-warning">
2.3.1. En utilisant l’ondelette sym6, traitez l’image Lenna_s.tif en ajustant de nouveau les paramètres à votre disposition.

<b>Remarque :</b> Les extrémités du défaut affectant l’image Lenna_s.tif ont les coordonnées suivantes : A = (0.1, 0.4) et B = (0.9, 0.6).
</div>

In [16]:
# Inscrivez votre code ici

<div class="alert alert-block alert-warning">
2.3.2. Comparez les résultats à ceux obtenus avec l’image Lenna_r.tif. Commentez. </div>

In [17]:
# Inscrivez votre code ici

<div class="alert alert-block alert-info">

### 2.4. Effet du type d’image (2 pts)
</div>
<div class="alert alert-block alert-warning">
2.4.1 Toujours avec l’ondelette sym6, traitez l’image phare_s.tif, dont le défaut a les mêmes caractéristiques que celui présent dans l’image Lenna_s.tif.

</div>

In [18]:
# Inscrivez votre code ici

<div class="alert alert-block alert-warning">
2.4.2. Que constatez-vous ? Interprétez votre résultat en vous appuyant différences entre les caractéristiques locales des images Lenna_s.tif et phare_s.tif. </div>

<div class="alert alert-block alert-success"> 
DOUBLE-CLIQUEZ POUR INSCRIRE VOTRE RÉPONSE
</div>